# VOCS data structure 

Variables, Objectives, Constraints, and other Settings (VOCS) helps define our optimization problems. 

In [1]:
from xopt.vocs import VOCS
from xopt.vocs import form_objective_data
import pandas as pd
import numpy as np

In [2]:
Y = """
variables:
  a: [0, 1e3] # Note that 1e3 usually parses as a str with YAML. 
  b: [-1, 1]
objectives:
  c: maximize
  d: minimize 
constraints:
  e: ['Less_than', 2]
  f: ['greater_than', 0]
constants:
  g: 1234

"""

vocs = VOCS.from_yaml(Y)
vocs

VOCS(variables={'a': [0.0, 1000.0], 'b': [-1.0, 1.0]}, constraints={'e': ['LESS_THAN', 2.0], 'f': ['GREATER_THAN', 0.0]}, objectives={'c': 'MAXIMIZE', 'd': 'MINIMIZE'}, constants={'g': 1234}, observables=[])

In [3]:
# as dict
dict(vocs)

{'variables': {'a': [0.0, 1000.0], 'b': [-1.0, 1.0]},
 'constraints': {'e': ['LESS_THAN', 2.0], 'f': ['GREATER_THAN', 0.0]},
 'objectives': {'c': 'MAXIMIZE', 'd': 'MINIMIZE'},
 'constants': {'g': 1234},
 'observables': []}

In [4]:
#  re-parse dict
vocs2 = VOCS.from_dict(dict(vocs))

In [5]:
# Check that these are the same
vocs2 == vocs

True

In [6]:
# This replaces the old vocs["variables"]
getattr(vocs, "variables")

{'a': [0.0, 1000.0], 'b': [-1.0, 1.0]}

In [7]:
vocs.objectives["c"] == "MAXIMIZE"

True

In [8]:
# json
vocs.to_json()

'{"variables":{"a":[0.0,1000.0],"b":[-1.0,1.0]},"constraints":{"e":["LESS_THAN",2.0],"f":["GREATER_THAN",0.0]},"objectives":{"c":"MAXIMIZE","d":"MINIMIZE"},"constants":{"g":1234},"observables":[]}'

# Objective Evaluation

In [9]:
data = pd.DataFrame(vocs.random_inputs(10))
# Add some outputs
data["c"] = data["a"] + data["b"]
data["d"] = data["a"] - data["b"]
data["e"] = data["a"] * 2 + data["b"] * 2
data["f"] = data["a"] * 2 - data["b"] * 2
data.index = np.arange(len(data)) + 5  # custom index
data

a         b     g           c           d            e  \
5    27.126897 -0.364478  1234   26.762420   27.491375    53.524839   
6   306.471146 -0.875397  1234  305.595749  307.346543   611.191498   
7   198.513291  0.552709  1234  199.066001  197.960582   398.132002   
8   251.735536 -0.809030  1234  250.926506  252.544566   501.853012   
9   611.565673  0.103141  1234  611.668814  611.462532  1223.337628   
10  299.211735  0.779981  1234  299.991715  298.431754   599.983431   
11  837.114707 -0.883538  1234  836.231170  837.998245  1672.462339   
12  527.008957 -0.898737  1234  526.110220  527.907694  1052.220439   
13  822.891936 -0.151750  1234  822.740186  823.043685  1645.480372   
14  580.734676 -0.739317  1234  579.995359  581.473993  1159.990719   

              f  
5     54.982749  
6    614.693086  
7    395.921164  
8    505.089132  
9   1222.925063  
10   596.863508  
11  1675.996490  
12  1055.815387  
13  1646.087371  
14  1162.947985

In [10]:
vocs.objectives

{'c': 'MAXIMIZE', 'd': 'MINIMIZE'}

In [11]:
# These are in standard form for minimization
form_objective_data(vocs.objectives, data)

objective_c  objective_d
5    -26.762420    27.491375
6   -305.595749   307.346543
7   -199.066001   197.960582
8   -250.926506   252.544566
9   -611.668814   611.462532
10  -299.991715   298.431754
11  -836.231170   837.998245
12  -526.110220   527.907694
13  -822.740186   823.043685
14  -579.995359   581.473993

In [12]:
# This is also available as a method
vocs.objective_data(data)

objective_c  objective_d
5    -26.762420    27.491375
6   -305.595749   307.346543
7   -199.066001   197.960582
8   -250.926506   252.544566
9   -611.668814   611.462532
10  -299.991715   298.431754
11  -836.231170   837.998245
12  -526.110220   527.907694
13  -822.740186   823.043685
14  -579.995359   581.473993

In [13]:
# use the to_numpy() method to convert for low level use.
vocs.objective_data(data).to_numpy()

array([[ -26.76241951,   27.49137473],
       [-305.59574911,  307.34654317],
       [-199.06600078,  197.96058205],
       [-250.926506  ,  252.54456589],
       [-611.66881389,  611.4625316 ],
       [-299.99171527,  298.43175395],
       [-836.23116963,  837.99824506],
       [-526.11021958,  527.90769353],
       [-822.74018604,  823.04368536],
       [-579.99535931,  581.47399263]])

In [14]:
vocs.constraint_data(data)

constraint_e  constraint_f
5      51.524839    -54.982749
6     609.191498   -614.693086
7     396.132002   -395.921164
8     499.853012   -505.089132
9    1221.337628  -1222.925063
10    597.983431   -596.863508
11   1670.462339  -1675.996490
12   1050.220439  -1055.815387
13   1643.480372  -1646.087371
14   1157.990719  -1162.947985

In [15]:
vocs.feasibility_data(data)

feasible_e  feasible_f  feasible
5        False        True     False
6        False        True     False
7        False        True     False
8        False        True     False
9        False        True     False
10       False        True     False
11       False        True     False
12       False        True     False
13       False        True     False
14       False        True     False

In [16]:
# normalize inputs to unit domain [0,1]
normed_data = vocs.normalize_inputs(data)
normed_data

a         b
5   0.027127  0.317761
6   0.306471  0.062301
7   0.198513  0.776355
8   0.251736  0.095485
9   0.611566  0.551571
10  0.299212  0.889990
11  0.837115  0.058231
12  0.527009  0.050632
13  0.822892  0.424125
14  0.580735  0.130342

In [17]:
# and denormalize
vocs.denormalize_inputs(normed_data)

a         b
5    27.126897 -0.364478
6   306.471146 -0.875397
7   198.513291  0.552709
8   251.735536 -0.809030
9   611.565673  0.103141
10  299.211735  0.779981
11  837.114707 -0.883538
12  527.008957 -0.898737
13  822.891936 -0.151750
14  580.734676 -0.739317

# Error handling

In [18]:
Y = """
variables:
  a: [0, 1e3] # Note that 1e3 usually parses as a str with YAML. 
  b: [-1, 1]
objectives:
  c: maximize
  d: minimize 
constraints:
  e: ['Less_than', 2]
  f: ['greater_than', 0]
constants:
  g: 1234

"""

vocs = VOCS.from_yaml(Y)

In [19]:
d = {"a": [1, 2, 3]}

df = pd.DataFrame(d)
df2 = pd.DataFrame(df).copy()

df2["b"] = np.nan
df2["b"] - 1

0   NaN
1   NaN
2   NaN
Name: b, dtype: float64

In [20]:
data["a"] = np.nan

In [21]:
a = 2


def f(x=a):
    return x


a = 99
f()

2

In [22]:
pd.DataFrame(6e66, index=[1, 2, 3], columns=["A"])

A
1  6.000000e+66
2  6.000000e+66
3  6.000000e+66

In [23]:
# These are in standard form for minimization

data = pd.DataFrame({"c": [1, 2, 3, 4]}, index=[9, 3, 4, 5])

form_objective_data(vocs.objectives, data)

objective_c  objective_d
9         -1.0          inf
3         -2.0          inf
4         -3.0          inf
5         -4.0          inf